# Italian Day-Ahead prices

In [1]:
import glob
import math
from datetime import datetime

import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

### Concat xlsx sheets

In [2]:
paths = glob.glob('../data/raw_data/historic_prices/*')
price_df_list = []
for path in paths:
    price_df_list.append(pd.read_excel(path, sheet_name='Prezzi-Prices'))

price_df = pd.concat(price_df_list, axis=0)
price_df.rename({'   Data/Date\n(YYYYMMDD)': 'date', 'Ora\n/Hour': 'hour'}, axis=1, inplace=True)
price_df.date = pd.to_datetime(price_df.date, format='%Y%m%d').dt.normalize()
price_df.sort_values('date', inplace=True)
price_df.to_csv('../data/clean_data/wholesale_price.csv')
price_df

date  hour        PUN       AUST        BSP       CNOR       COAC  \
0    2019-01-01     1   51.00000   51.00000   51.00000   51.00000   51.00000   
23   2019-01-01    24   54.90516   54.90516   54.90516   54.90516   54.90516   
22   2019-01-01    23   58.65000   58.65000   58.65000   58.65000   58.65000   
21   2019-01-01    22   62.75007   61.72000   61.72000   61.72000   61.72000   
20   2019-01-01    21   65.98689   64.23000   64.23000   64.23000   64.23000   
...         ...   ...        ...        ...        ...        ...        ...   
8740 2022-12-31     5  189.20000  189.20000  189.20000  189.20000  189.20000   
8739 2022-12-31     4  186.00000  186.00000  186.00000  186.00000  186.00000   
8738 2022-12-31     3  157.00000  157.00000  157.00000  157.00000  157.00000   
8748 2022-12-31    13  187.59000  187.59000  187.59000  187.59000  187.59000   
8758 2022-12-31    23  217.78000  217.78000  217.78000  217.78000  217.78000   

           CORS       CSUD       FRAN  ...      ROSN       SARD       SICI  \
0      51.00000   51.00000   51.00000  ...  51.00000   51.00000   51.00000   
23     54.90516   54.90516   54.90516  ...  54.90516   54.90516   54.90516   
22     58.65000   58.65000   58.65000  ...  58.65000   58.65000   58.65000   
21     61.72000   61.72000   61.72000  ...  61.72000   61.72000   74.97000   
20     64.23000   64.23000   64.23000  ...  64.23000   64.23000   87.00000   
...         ...        ...        ...  ...       ...        ...        ...   
8740  189.20000  189.20000  189.20000  ...       NaN  189.20000  189.20000   
8739  186.00000  186.00000  186.00000  ...       NaN  186.00000  186.00000   
8738  157.00000  157.00000  157.00000  ...       NaN  157.00000  157.00000   
8748  187.59000  187.59000  187.59000  ...       NaN  187.59000  187.59000   
8758  217.78000  217.78000  217.78000  ...       NaN  217.78000  217.78000   

           SLOV        SUD       SVIZ       XAUS       XFRA    CALA    XGRE  
0      51.00000   51.00000   51.00000   51.00000   51.00000     NaN     NaN  
23     54.90516   54.90516   54.90516   54.90516   54.90516     NaN     NaN  
22     58.65000   58.65000   58.65000   58.65000   58.65000     NaN     NaN  
21     61.72000   61.72000   61.72000   61.72000   61.72000     NaN     NaN  
20     64.23000   64.23000   64.23000   64.23000   64.23000     NaN     NaN  
...         ...        ...        ...        ...        ...     ...     ...  
8740  189.20000  189.20000  189.20000  189.20000  189.20000  189.20  189.20  
8739  186.00000  186.00000  186.00000  186.00000  186.00000  186.00  186.00  
8738  157.00000  157.00000  157.00000  157.00000  157.00000  157.00  157.00  
8748  187.59000  187.59000  187.59000  187.59000  187.59000  187.59  187.59  
8758  217.78000  217.78000  217.78000  217.78000  217.78000  217.78  217.78  

[35064 rows x 24 columns]

### Convert UK data to EUR and merge

In [3]:
epex_price_df = pd.read_csv('../data/raw_data/EPEX_and_N2EX_DA_WD_PRICES.csv')[['SETTLEMENT_DATE', 'SETTLEMENT_PERIOD', 'EPEX_HH_DA']]
epex_price_df.columns = ['date', 'sp', 'gb_price_gbp']
epex_price_df.date = pd.to_datetime(epex_price_df.date)
epex_price_df['hour'] = epex_price_df.sp.apply(lambda x: math.ceil(x/2))
conversion_df = pd.read_csv('../data/raw_data/euro-british-pound-exchange-rate-historical-chart.csv', skiprows=15)
conversion_df.rename({' value': 'conversion'}, axis=1, inplace=True)
conversion_df.date = pd.to_datetime(conversion_df.date)
epex_price_df = pd.merge(epex_price_df, conversion_df, on='date', how='left')
epex_price_df['gb_price_eur'] = epex_price_df.gb_price_gbp * epex_price_df.conversion
epex_price_df

date  sp  gb_price_gbp  hour  conversion  gb_price_eur
0     2022-01-01   1          75.0     1      0.8404      63.03000
1     2022-01-01   2          75.0     1      0.8404      63.03000
2     2022-01-01   3          91.2     2      0.8404      76.64448
3     2022-01-01   4          48.0     2      0.8404      40.33920
4     2022-01-01   5          70.0     3      0.8404      58.82800
...          ...  ..           ...   ...         ...           ...
17515 2022-12-31  44         129.3    22      0.8867     114.65031
17516 2022-12-31  45         135.0    23      0.8867     119.70450
17517 2022-12-31  46          91.0    23      0.8867      80.68970
17518 2022-12-31  47          40.0    24      0.8867      35.46800
17519 2022-12-31  48          17.4    24      0.8867      15.42858

[17520 rows x 6 columns]

In [4]:
price_df = pd.merge(price_df, epex_price_df, on=['date', 'hour'], how='left')
price_df.head()

date  hour       PUN      AUST       BSP      CNOR      COAC  \
0 2019-01-01     1  51.00000  51.00000  51.00000  51.00000  51.00000   
1 2019-01-01    24  54.90516  54.90516  54.90516  54.90516  54.90516   
2 2019-01-01    23  58.65000  58.65000  58.65000  58.65000  58.65000   
3 2019-01-01    22  62.75007  61.72000  61.72000  61.72000  61.72000   
4 2019-01-01    21  65.98689  64.23000  64.23000  64.23000  64.23000   

       CORS      CSUD      FRAN  ...       SUD      SVIZ      XAUS      XFRA  \
0  51.00000  51.00000  51.00000  ...  51.00000  51.00000  51.00000  51.00000   
1  54.90516  54.90516  54.90516  ...  54.90516  54.90516  54.90516  54.90516   
2  58.65000  58.65000  58.65000  ...  58.65000  58.65000  58.65000  58.65000   
3  61.72000  61.72000  61.72000  ...  61.72000  61.72000  61.72000  61.72000   
4  64.23000  64.23000  64.23000  ...  64.23000  64.23000  64.23000  64.23000   

   CALA  XGRE  sp  gb_price_gbp  conversion  gb_price_eur  
0   NaN   NaN NaN           NaN         NaN           NaN  
1   NaN   NaN NaN           NaN         NaN           NaN  
2   NaN   NaN NaN           NaN         NaN           NaN  
3   NaN   NaN NaN           NaN         NaN           NaN  
4   NaN   NaN NaN           NaN         NaN           NaN  

[5 rows x 28 columns]

### Plot data

In [7]:
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=price_df.date,
    y=price_df.PUN,
    name='Hourly',
    line=dict(color='lightgrey', width=0.5)
))
fig.add_trace(go.Scatter(
    x=price_df.date,
    y=price_df.PUN.rolling(24).mean(),
    name='Daily',
    line=dict(color='cornflowerblue', width=1)
))
fig.add_trace(go.Scatter(
    x=price_df.date,
    y=price_df.PUN.rolling(336).mean(),
    name='Month',
    line=dict(color='crimson', width=2)
))

fig.update_layout(
    title='National Price (PUN) - buy price',
    yaxis_title='€/MWh',
    template='plotly_white'
)

fig.write_image('../figures/historic-pun.jpeg', scale=2, engine='orca')
fig

In [6]:
fig = px.bar(
    price_df.loc[price_df.date > datetime(2022, 1, 1)][['CNOR', 'CSUD', 'NORD', 'SARD', 'SUD']].mean(),
    labels={'value': '€/MWh', 'index': ''}
    )

fig.update_layout(
    title='2022 average zonal clearing price - sell price',
    showlegend=False,
    yaxis_range=[280, 310]
)

fig